In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
# Imports
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader
import pandas as pd

from lion_pytorch import Lion

In [3]:
from vae import VAE
from vae import GroupSoftmax
from trainer import Trainer

In [4]:
# just workspace if you are using the docker container

directory_path = '/mnt/c/Users/fabi8/Desktop/GNN'

In [ ]:
# default parameters
#gamma = 2 
#beta = 1 
#hidden_dim = 750
#latent_dim = 50

In [5]:
# to test parameter list 
gammas = [1, 2, 3, 4, 5]
betas = [1, 2, 3, 4, 5]
hidden_dims = [100, 250, 500, 750, 1000]
latent_dims = [10, 25, 50, 75, 100, 200]


In [6]:
alpha = .125

# default_parameters
gamma = 2
beta = 1 
hidden_dim = 500
latent_dim = 100

data_set = 'one_hot_pNaNs_agep_small.csv'
#intermediate_models = f'best_model_small_l{50}.pth'
#output_model = f'model_small_l50.pth'

In [7]:
# Device config 
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Device: {device}")

Device: cuda


In [8]:
# input size not updated
group_sizes = [2, 5, 5, 11, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 19, 19, 19, 19, 19, 19, 19, 19, 19, 19, 19, 19, 19, 19, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7]
test = VAE(433, 1000, 6, 50, group_sizes)

total_params = sum(p.numel() for p in test.parameters())
trainable_params = sum(p.numel() for p in test.parameters() if p.requires_grad)
print(trainable_params)


25095599


In [9]:
# Dataset import 
# Windows path
# data = pd.read_csv('A:/csv_hus/psam_hus_pus_filtered.csv')
# WSL path
data = pd.read_csv(f'{directory_path}/data/{data_set}')

In [10]:
cols = list(data.columns)
cols = [col.split(":")[0] for col in cols]

onehot_counts = {col: sum(data.columns.str.startswith(f"{col}:")) for col in cols}
print(list(onehot_counts.values()))


input_dim = sum(onehot_counts.values())
print(input_dim)

[2, 5, 5, 11, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 19, 19, 19, 19, 19, 19, 19, 19, 19, 19, 19, 19, 19, 19, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7]
433


In [11]:
# Data loader 

data_tensor = torch.tensor(data.values, dtype=torch.float32)
data_loader = DataLoader(data_tensor, batch_size=len(data_tensor), shuffle=True)

# Class_sizes 
group_sizes = list(onehot_counts.values())


In [12]:
# loop over different hyper parameters 
for i in gammas:
    intermediate_models = f'bms_l{latent_dim}_h{hidden_dim}_b{beta}_g{i}.pth'
    intermediate_path = f'{directory_path}/models/{intermediate_models}'
    output_model = f'model_l{latent_dim}_h{hidden_dim}_b{beta}_g{i}.pth'
    model = VAE(input_dim, hidden_dim, 6, latent_dim, group_sizes)
    optimizer = Lion(model.parameters(), lr=1e-3)
    trainer = Trainer(model, optimizer, device)
    trainer.train(data_loader, epochs=4000, disk_path=intermediate_path, gamma=i, alpha=alpha, beta=beta)
    torch.save(model.state_dict(), f'{directory_path}/models/{output_model}')

Epoch 0, Loss: 20.9085693359375, LR: 0.001
Epoch 1, Loss: 13871349760000.0, LR: 0.001
Epoch 2, Loss: 14140663.0, LR: 0.001
Epoch 3, Loss: 518320.96875, LR: 0.001
Epoch 4, Loss: 39491.71484375, LR: 0.001
Epoch 5, Loss: 998.85498046875, LR: 0.001
Epoch 6, Loss: 124.164306640625, LR: 0.001
Epoch 7, Loss: 65.34365844726562, LR: 0.001
Epoch 8, Loss: 45.46367645263672, LR: 0.001
Epoch 9, Loss: 38.3834228515625, LR: 0.001
Epoch 10, Loss: 36.28069305419922, LR: 0.001
Epoch 11, Loss: 35.00666046142578, LR: 0.001
Epoch 12, Loss: 32.788082122802734, LR: 0.001
Epoch 13, Loss: 30.756025314331055, LR: 0.001
Epoch 14, Loss: 29.228878021240234, LR: 0.001
Epoch 15, Loss: 28.88654327392578, LR: 0.001
Epoch 16, Loss: 28.912511825561523, LR: 0.001
Epoch 17, Loss: 27.96009063720703, LR: 0.001
Epoch 18, Loss: 26.543798446655273, LR: 0.001
Epoch 19, Loss: 25.325519561767578, LR: 0.001
Epoch 20, Loss: 24.471420288085938, LR: 0.001
Epoch 21, Loss: 23.261234283447266, LR: 0.001
Epoch 22, Loss: 22.86476898193359

In [13]:
for i in betas:
    intermediate_models = f'bms_l{latent_dim}_h{hidden_dim}_b{i}_g{gamma}.pth'
    intermediate_path = f'{directory_path}/models/{intermediate_models}'
    output_model = f'model_l{latent_dim}_h{hidden_dim}_b{i}_g{gamma}.pth'
    model = VAE(input_dim, hidden_dim, 6, latent_dim, group_sizes)
    optimizer = Lion(model.parameters(), lr=1e-3)
    trainer = Trainer(model, optimizer, device)
    trainer.train(data_loader, epochs=4000, disk_path=intermediate_path, gamma=gamma, alpha=alpha, beta=i)
    torch.save(model.state_dict(), f'{directory_path}/models/{output_model}')

Epoch 0, Loss: 14.475208282470703, LR: 0.001
Epoch 1, Loss: 4416671.5, LR: 0.001
Epoch 2, Loss: 448.3974304199219, LR: 0.001
Epoch 3, Loss: 14.82199478149414, LR: 0.001
Epoch 4, Loss: 10.64423656463623, LR: 0.001
Epoch 5, Loss: 10.089609146118164, LR: 0.001
Epoch 6, Loss: 9.626703262329102, LR: 0.001
Epoch 7, Loss: 9.310897827148438, LR: 0.001
Epoch 8, Loss: 9.132076263427734, LR: 0.001
Epoch 9, Loss: 8.976701736450195, LR: 0.001
Epoch 10, Loss: 9.153863906860352, LR: 0.001
Epoch 11, Loss: 9.090385437011719, LR: 0.001
Epoch 12, Loss: 9.050507545471191, LR: 0.001
Epoch 13, Loss: 9.074121475219727, LR: 0.001
Epoch 14, Loss: 9.19444751739502, LR: 0.001
Epoch 15, Loss: 9.333928108215332, LR: 0.001
Epoch 16, Loss: 9.567770004272461, LR: 0.001
Epoch 17, Loss: 9.787665367126465, LR: 0.001
Epoch 18, Loss: 10.157832145690918, LR: 0.001
Epoch 19, Loss: 10.497573852539062, LR: 0.001
Epoch 20, Loss: 10.964804649353027, LR: 0.001
Epoch 21, Loss: 11.353921890258789, LR: 0.001
Epoch 22, Loss: 11.9059

In [14]:
for i in hidden_dims:
    intermediate_models = f'bms_l{latent_dim}_h{i}_b{beta}_g{gamma}.pth'
    intermediate_path = f'{directory_path}/models/{intermediate_models}'
    output_model = f'model_l{latent_dim}_h{i}_b{beta}_g{gamma}.pth'
    model = VAE(input_dim, i, 6, latent_dim, group_sizes)
    optimizer = Lion(model.parameters(), lr=1e-3)
    trainer = Trainer(model, optimizer, device)
    trainer.train(data_loader, epochs=4000, disk_path=intermediate_path, gamma=gamma, alpha=alpha, beta=beta)
    torch.save(model.state_dict(), f'{directory_path}/models/{output_model}')

Epoch 0, Loss: 196.1019287109375, LR: 0.001
Epoch 1, Loss: 13.460867881774902, LR: 0.001
Epoch 2, Loss: 13.281652450561523, LR: 0.001
Epoch 3, Loss: 12.485880851745605, LR: 0.001
Epoch 4, Loss: 12.033754348754883, LR: 0.001
Epoch 5, Loss: 11.499883651733398, LR: 0.001
Epoch 6, Loss: 11.662331581115723, LR: 0.001
Epoch 7, Loss: 11.074122428894043, LR: 0.001
Epoch 8, Loss: 10.841782569885254, LR: 0.001
Epoch 9, Loss: 11.431509971618652, LR: 0.001
Epoch 10, Loss: 10.532155990600586, LR: 0.001
Epoch 11, Loss: 10.522517204284668, LR: 0.001
Epoch 12, Loss: 10.09002685546875, LR: 0.001
Epoch 13, Loss: 9.924421310424805, LR: 0.001
Epoch 14, Loss: 9.741122245788574, LR: 0.001
Epoch 15, Loss: 9.78390884399414, LR: 0.001
Epoch 16, Loss: 9.722306251525879, LR: 0.001
Epoch 17, Loss: 9.585088729858398, LR: 0.001
Epoch 18, Loss: 9.439826965332031, LR: 0.001
Epoch 19, Loss: 9.334001541137695, LR: 0.001
Epoch 20, Loss: 9.170025825500488, LR: 0.001
Epoch 21, Loss: 9.368720054626465, LR: 0.001
Epoch 22, 

In [15]:
for i in latent_dims:
    intermediate_models = f'bms_l{i}_h{hidden_dim}_b{beta}_g{gamma}.pth'
    intermediate_path = f'{directory_path}/models/{intermediate_models}'
    output_model = f'model_l{i}_h{hidden_dim}_b{beta}_g{gamma}.pth'
    model = VAE(input_dim, hidden_dim, 6, i, group_sizes)
    optimizer = Lion(model.parameters(), lr=1e-3)
    trainer = Trainer(model, optimizer, device)
    trainer.train(data_loader, epochs=4000, disk_path=intermediate_path, gamma=gamma, alpha=alpha, beta=beta)
    torch.save(model.state_dict(), f'{directory_path}/models/{output_model}')
    

Epoch 0, Loss: 14.530095100402832, LR: 0.001
Epoch 1, Loss: 720009.6875, LR: 0.001
Epoch 2, Loss: 13.63827896118164, LR: 0.001
Epoch 3, Loss: 11.324583053588867, LR: 0.001
Epoch 4, Loss: 10.872567176818848, LR: 0.001
Epoch 5, Loss: 10.358942985534668, LR: 0.001
Epoch 6, Loss: 10.324642181396484, LR: 0.001
Epoch 7, Loss: 10.125606536865234, LR: 0.001
Epoch 8, Loss: 9.922955513000488, LR: 0.001
Epoch 9, Loss: 9.815805435180664, LR: 0.001
Epoch 10, Loss: 9.804128646850586, LR: 0.001
Epoch 11, Loss: 9.730589866638184, LR: 0.001
Epoch 12, Loss: 9.625964164733887, LR: 0.001
Epoch 13, Loss: 9.53807258605957, LR: 0.001
Epoch 14, Loss: 9.566933631896973, LR: 0.001
Epoch 15, Loss: 9.403974533081055, LR: 0.001
Epoch 16, Loss: 9.53533935546875, LR: 0.001
Epoch 17, Loss: 9.409934997558594, LR: 0.001
Epoch 18, Loss: 9.502556800842285, LR: 0.001
Epoch 19, Loss: 9.424445152282715, LR: 0.001
Epoch 20, Loss: 9.362194061279297, LR: 0.001
Epoch 21, Loss: 9.413208961486816, LR: 0.001
Epoch 22, Loss: 9.2883

In [ ]:
# test the beta decay 
beta = 5
gamma = 2
alpha = .123
hidden_dim = 500
latent_dim = 100


model = VAE(input_dim, hidden_dim, 6, latent_dim, group_sizes)
optimizer = Lion(model.parameters(), lr=1e-3)
trainer = Trainer(model, optimizer, device)
trainer.train(data_loader, epochs=4000, disk_path=None, gamma=gamma, alpha=alpha, beta=beta)